#Implementing Data Transformation Pipelines

We’ll implement data pipelines using PySpark to:
- Filter and Transform the data.
- Enrich it for BI requirements (e.g., calculate aggregates, derive new features).
- Optimize the pipeline for scalability and performance.

In [0]:
# Import necessary libraries
from pyspark.sql.functions import avg, count, desc, col

# Paths to BI schema data in S3
bi_path = "dbfs:/mnt/de-yelpdataset-raw/yelpdataset/star-schema-bidata/"
dim_business = spark.read.parquet(bi_path + "dim_business")
dim_user = spark.read.parquet(bi_path + "dim_user")
dim_time = spark.read.parquet(bi_path + "dim_time")
fact_reviews = spark.read.parquet(bi_path + "fact_reviews")

#Business Insights Pipeline
Identifying top businesses by review count and average rating

In [0]:
#Joins fact_reviews with dim_business.
#Aggregates review counts and average ratings.
#Filters businesses with over 50 reviews and ratings ≥ 4.0.
#Outputs the top businesses by rating and reviews.

business_insights = fact_reviews.join(dim_business, "business_id") \
    .groupBy("business_id", "name", "categories", "city", "state") \
    .agg(
        count("review_id").alias("total_reviews"),
        avg("rating").alias("average_rating")
    ) \
    .filter(col("total_reviews") > 50) \
    .filter(col("average_rating") >= 4.0) \
    .orderBy(desc("average_rating"), desc("total_reviews"))

#Displaying the top businesses by rating and reviews.

In [0]:
#Displaying the top businesses by rating and reviews.
business_insights.display()

business_id name categories city state total_reviews average_rating 1RqfozJoosHAsKZhc5PY7w Walls Jewelry Repairing Watch Repair, Local Services, Shopping, Jewelry Nashville TN 114 5.0 -siOxQQcGKtb-04dX0Cxnw ella & louie flowers Flowers & Gifts, Florists, Shopping, Event Planning & Services, Floral Designers Santa Barbara CA 104 5.0 4-P4Bzqd01YvKX9tp7IGfQ Drink & Learn Beer, Wine & Spirits, Hotels & Travel, Food, Tours New Orleans LA 90 5.0 dhLARBhUnJloLa8xZ1Stpw Steves iPhone Repair Professional Services, Local Services, Electronics Repair, Mobile Phone Repair, IT Services & Computer Repair Cherry Hill NJ 78 5.0 LTqm4uY4GIYHfzuh5pVZNQ Jeramie Lu Photography Event Photography, Event Planning & Services, Photographers, Session Photography Reno NV 77 5.0 x-SCuOwghy4GlZdVOKjt4g Twisted Twig Fine Florals Florists, Event Planning & Services, Shopping, Flowers & Gifts, Party & Event Planning Santa Barbara CA 74 5.0 2FQoAp9w0G_NhuZMqo9bfA ByCherry Photography Session Photography, Wedding Planning, Event Planning & Services, Event Photography, Photographers, Photo Booth Rentals Santa Barbara CA 73 5.0 DnkpXhc5DKdeBT-0jG13JQ Carpinteria Lock & Key Security Systems, Keys & Locksmiths, Home Services Carpinteria CA 70 5.0 NLx84Im37HcZkcFBO2cxlw Jack & Melody Cote - Chase International, Reno Real Estate Real Estate Agents, Home Services, Real Estate, Real Estate Services Reno NV 69 5.0 v8I7yA-t1onNs2Ce81J2MQ A Beloved Friends Pet Crematory Of Northern Nevada Local Services, Pet Services, Funeral Services & Cemeteries, Pets, Pet Cremation Services Reno NV 68 5.0 _LHkm-m9a_IDqfqfdWggHQ Dj Hecktik Photo Booth Rentals, Performing Arts, Event Planning & Services, Party & Event Planning, DJs, Arts & Entertainment, Wedding Planning, Audio/Visual Equipment Rental, Party Supplies, Party Equipment Rentals Santa Barbara CA 68 5.0 CBPodZLpZVUREZBd-pIp7Q Delacruz Chiropractic Chiropractors, Health & Medical, Doctors Reno NV 67 5.0 xvQVM5I98wKlHWk6Tk_rgA AllVitae Health & Chiropractic Massage, Chiropractors, Skin Care, Beauty & Spas, Weight Loss Centers, Health & Medical, Health Coach, Massage Therapy Tampa FL 67 5.0 YSTaLnxXEvNhby0SEu-5KA Sugar Hair Removal, Waxing, Eyelash Service, Beauty & Spas, Sugaring Santa Barbara CA 66 5.0 lsDHBMfJ38pX_0I91OaHLg Gators Parasail Sport Equipment Hire, Parasailing, Hotels & Travel, Tours, Active Life Madeira Beach FL 66 5.0 3Ekl1I4xBRR3Yf2hBqQFhQ Tint Works Window Tinting Auto Glass Services, Auto Customization, Automotive, Home Services, Home Window Tinting, Car Window Tinting Santa Barbara CA 65 5.0 LTa-23WGNMC37_b2mm5jkQ Walden Floral LA & Nashville Shopping, Flowers & Gifts, Florists, Event Planning & Services, Wedding Planning Nashville TN 64 5.0 XysLDlS6X37LxMJ3VbUp-Q Seb Boxing Fitness & Instruction, Boxing, Trainers, Active Life Franklin TN 63 5.0 oDnnlCOYpkMZwOv0oFSp4A Truong & Company Jeweler Local Services, Jewelry, Shopping, Jewelry Repair Santa Barbara CA 61 5.0 NfKcglAqZ3eZMIepH1YwYw Matt Glynn - Schumacher Mortgage Real Estate, Mortgage Brokers, Financial Services, Home Services, Mortgage Lenders Nashville TN 60 5.0 eK-_ahKKaMUQ1b0F1PRgMw Let's Sweat Fitness & Instruction, Gyms, Active Life, Yoga, Cycling Classes Tucson AZ 59 5.0 7Of0lOwKOe5lYwRBs_uRtQ Pivotal Touch Healing Professional Services, Life Coach, Supernatural Readings, Tui Na, Traditional Chinese Medicine, Arts & Entertainment, Beauty & Spas, Reiki, Health & Medical, Hypnosis/Hypnotherapy, Massage Therapy, Massage Brentwood TN 58 5.0 7_Hz9ORTZ7zFJRRShyKExA Guldner's Collision Service Automotive, Body Shops Philadelphia PA 57 5.0 frSbEquWLwfVe6KxH_2QAw Premier Pest Solutions Local Services, Pest Control Tucson AZ 56 5.0 pl87HrR7JYUAH7ULEwj7UQ Marc Bosserman Pianist & Vocalist Arts & Entertainment, Musicians, Performing Arts, Music Production Services, Party & Event Planning, Professional Services, Wedding Planning, Event Planning & Services Tampa Bay FL 55 5.0 xDLoMSXpK5ZQUh6WJ1PZLg Campbell Jewelers Bridal, Shopping, Jewelry Repair, Jewelr

# User Insights Pipeline
Identifying top users by total reviews

In [0]:
#Joins fact_reviews with dim_user.
#Aggregates total reviews and average ratings given by users.
#Outputs the most active users.

user_insights = fact_reviews.join(dim_user, "user_id") \
    .groupBy("user_id", "name") \
    .agg(
        count("review_id").alias("total_reviews"),
        avg("rating").alias("average_rating_given")
    ) \
    .orderBy(desc("total_reviews"))

#Displaying the top users by total reviews and average rating given.

In [0]:
user_insights.display()

user_id name total_reviews average_rating_given _BcWyKQL16ndpBdggh2kNA Karen 3048 3.6377952755905514 Xw7ZjaGfr0WNVt6s_5KZfA Marielle 1840 4.072826086956522 0Igx-a1wAstiBDerGxXk2A Jen 1747 3.9902690326273613 -G7Zkl1wIWBBmD0KRy_sCw Gerald 1682 3.652794292508918 ET8n-r7glWYqZhuR6GcdNw Michelle 1653 4.046581972171809 bYENop4BuQepBjM1-BI3fA Steven 1578 3.8536121673003803 1HM81n6n4iPIFU5d2Lokhw Shannon 1554 3.045045045045045 fr1Hz2acAb3OaL3l6DyKNg Boon 1447 3.946786454733932 wXdbkFZsfDR7utJvbWElyA Ken 1396 4.210601719197708 Um5bfs5DH6eizgjH3xZsvg Dianna 1391 3.804457225017973 qjfMBIZpQT9DDtw_BWCopQ Rachel 1324 3.897280966767372 VL12EhEdT4OWqGq0nIqkzw Mark 1308 3.5053516819571864 bJ5FtCtZX3ZZacz2_2PJjA Bill 1298 4.083204930662558 pou3BbKsIozfH50rxmnMew Brett 1247 4.235765838011227 ouODopBKF3AqfCkuQEnrDg Danan 1129 3.604960141718335 B-s-8VUnuBjGTP3d01jsyw Allie 1087 3.6918123275069 -kLVfaJytOJY2-QdQoCcNQ Christina 1076 4.25092936802974 vHc-UrI9yfL_pnnc6nJtyQ Michael 1071 4.450980392156863 CfX4sTIFFNaRchNswqhVfg Christopher 1047 3.6198662846227316 AHRrG3T1gJpHvtpZ-K0G_g Brittany 1041 4.367915465898175 I2XpWCHAom1JRyHXZQrnfg Kathy 1023 3.3098729227761488 ppsm8EDKjA1fp1yTCP3RrQ Steve 978 3.652351738241309 AaJ9d4OrFmgc4S_U2QiSZg Steve 964 4.200207468879668 zYFGMy1_thjMnvQLX6JNBw Wanda 954 4.122641509433962 PnwOegp7RXfMeNAyO9fQhQ Michelle 947 3.668426610348469 2iS1vg5TYpV_iEiNC8osTg Peter 938 3.388059701492537 XzpJ4uHkxARCFQiZ9bffyg P 927 3.6030204962243797 eTvp_hYnsrI5-ow_sQ31_g Patt 922 3.9522776572668112 lYQk0R6sPfo3WeX-l_5BuA Christopher 917 3.2737186477644493 vffKQc_WQMYFGY4JS5VAOw michelle 900 3.8933333333333335 6s-g2vFu12OemhiK3FJuOQ Dave 888 3.6981981981981984 lAW03ccfMEuRZiDqvVgc0w Kristin 866 3.9584295612009237 0YI3p9o-ntRgRaPWpfa22Q Phil 863 3.9617612977983776 GcdYgbaF75vj7RO6EZhPOQ Kathleen 860 3.832558139534884 IKbjLnfBQtEyVzEu8CuOLg Erica 844 3.8661137440758293 vYMvOTL31e0KbTo9Hd0tjg Nick 834 4.046762589928058 r3QexFIhBXBT99canAgVEg Paula 830 3.6650602409638555 WwulXySQN8t2hwqH_yWurA Niki 829 4.568154402895054 h7p-GuaHFGsiKCF4g6Bjqg Alexis 829 3.506634499396864 OIDpKC2p61qVO_spPqw1qA Nicole 823 4.122721749696233 6ObFF8-uKnOAlXuSH4TlyQ Isabella 820 4.324390243902439 iPkdNziqnhNukjnmsrSzmg Kelly 790 3.949367088607595 E4BsVQnG5zetbwv2x8QIWg Charles 780 3.1243589743589744 kkPgJv6KBFN15caG7NYYlg Ali 773 3.7671410090556274 vmUqcqMjlWoBM6qfmUXgyQ James 772 4.597150259067358 FlXBpK_YZxLo27jcMdII1w Mallory 770 3.981818181818182 zUk_Ww2q1At1QSyRbUjIGQ Tricia 767 3.9308996088657104 sh3V6hnNMLVV9YwFA9QNaw Virginia 764 3.4528795811518322 A9cXP_K95FRor1qxuUEu2g Richard 758 3.7902374670184695 lMY8NBPyzlPbbu-KBYfD9A Christy 744 4.130376344086022 cufhYFdyrUAt4SWe-m0grQ John 742 3.8881401617250675 OLGQ7alK4VKl3YdQk6UF5g Michelle 733 3.806275579809004 nnImk681KaRqUVHlSfZjGQ Carlos 732 3.919398907103825 kA7sIBVKgWXVwWbpXsUHQg Kelleigh 729 3.9917695473251027 Sp2GV7D-_JLZMPQmDanzPQ Brigitte 725 3.8510344827586205 RCZ5M9o2-fxgFuurpmEs3w Craig 719 3.929068150208623 vFd8aBLg1kFcd0kCkoi-xw Retna 714 4.359943977591036 8EMU7d4pCkdqUnvlIW40CA Jeff 698 4.247851002865329 RwPKUrc0ae54hV1DWU1MsQ Mike 687 3.339155749636099 Oi1qbcz2m2SnwUeztGYcnQ Steven 675 3.4651851851851854 GfI-d9mQePFA2PvhAd4WGQ Robert 671 3.6885245901639343 5Y5KbsI5buMcNh2hTFaRpA Marcia 666 3.9354354354354353 R9IJ1Byr27n6wXj3QvJ2Lg Amy OO 664 4.0120481927710845 AQxmbuDiToMv2WYtq4Mfdw Les 662 3.678247734138973 3QnoTcrxuafMCoTzW_AH7A Sari Marissa 661 4.273827534039334 Zn8tgekH0oCfyk4SUtygoA Dave 660 4.081818181818182 gv0coNUFY-fibRwP8IKqPA Bob 659 3.1911987860394535 WO6L5yMX5LEeJuMNMjerRQ Jenny 658 3.6656534954407296 Jt3GylPuH64uA3zTdbMdCg Dana 658 4.37386018237082 -ZHlPAvlVdgtiu6DiCq7Yg DeAnna 657 3.538812785388128 cIVmIJD7nIiEcVGamfBoVw Jay 647 3.3369397217928904 Wjia69bHEb7xeWMlxWNPGA Karen 647 3.7434312210200926 JyzLjUFEIW3epNlHI6Oa6Q Ameesh 644 3.8059006211180124 47oIw-CN1guUKx2_vUdsgw Stephanie 641 3.7535101404056164 0G-QF457q_0Z_jKqh6xWiA Joi 640 4.1890625 LkXNQQaIc5yrKu9Ap87RrA Rober

# Time-Based Aggregates
 Aggregate reviews by month and year

In [0]:
#Joins fact_reviews with dim_time.
#Groups reviews by year and month.
#Calculates total reviews and average ratings per period.

time_aggregates = fact_reviews.join(dim_time, fact_reviews["date"] == dim_time["full_date"]) \
    .groupBy("year", "month") \
    .agg(
        count("review_id").alias("total_reviews"),
        avg("rating").alias("average_rating")
    ) \
    .orderBy("year", "month")

#Displaying aggregate reviews and average ratings by year and month.

In [0]:
time_aggregates.display()

year month total_reviews average_rating 2005 2 3 4.333333333333333 2005 3 74 3.6486486486486487 2005 4 26 4.153846153846154 2005 5 108 4.083333333333333 2005 6 38 4.026315789473684 2005 7 259 3.671814671814672 2005 8 66 4.166666666666667 2005 9 69 3.8840579710144927 2005 10 39 4.205128205128205 2005 11 70 3.842857142857143 2005 12 102 4.107843137254902 2006 1 221 3.986425339366516 2006 2 185 4.129729729729729 2006 3 191 4.052356020942408 2006 4 196 3.9183673469387754 2006 5 224 3.9642857142857144 2006 6 180 3.9944444444444445 2006 7 389 3.966580976863753 2006 8 492 3.975609756097561 2006 9 461 4.032537960954447 2006 10 433 3.928406466512702 2006 11 426 3.9107981220657275 2006 12 455 4.118681318681318 2007 1 802 3.8890274314214466 2007 2 1420 3.706338028169014 2007 3 1219 3.726825266611977 2007 4 1111 3.92979297929793 2007 5 908 3.9262114537444934 2007 6 1141 3.974583698510079 2007 7 1660 3.8939759036144577 2007 8 1665 3.9591591591591593 2007 9 1442 3.924410540915395 2007 10 1429 3.822253324002799 2007 11 1377 3.8177196804647786 2007 12 1189 3.821698906644239 2008 1 2111 3.861676930364756 2008 2 2228 3.8765709156193897 2008 3 2788 3.86441893830703 2008 4 3745 3.9054739652870496 2008 5 3796 3.9370389884088515 2008 6 4145 3.798552472858866 2008 7 5211 3.7353674918441757 2008 8 5596 3.753395282344532 2008 9 4611 3.7462589459986986 2008 10 4898 3.7429563086974276 2008 11 4689 3.760929835785882 2008 12 4408 3.7690562613430125 2009 1 5974 3.7587880816873116 2009 2 5058 3.7032423882957692 2009 3 6091 3.7230339845673943 2009 4 5539 3.707528434735512 2009 5 5513 3.7008888082713587 2009 6 5864 3.7401091405184173 2009 7 6844 3.713617767387493 2009 8 7303 3.7097083390387513 2009 9 6462 3.733364283503559 2009 10 6453 3.7207500387416705 2009 11 6570 3.7353120243531204 2009 12 6716 3.6868671828469326 2010 1 10745 3.715123313168916 2010 2 9289 3.7170847238669396 2010 3 10586 3.724447383336482 2010 4 9743 3.7043005234527353 2010 5 10135 3.722348297977306 2010 6 10256 3.7110959438377535 2010 7 12554 3.7451808188625137 2010 8 13490 3.7327650111193478 2010 9 12621 3.7135726170667933 2010 10 12988 3.701647674776717 2010 11 12875 3.7514563106796115 2010 12 13305 3.7112363773017663 2011 1 17766 3.736294044804683 2011 2 16763 3.733341287359065 2011 3 19571 3.737570895713045 2011 4 18467 3.710781393837656 2011 5 18971 3.701597174634969 2011 6 19664 3.706112693246542 2011 7 22397 3.7073715229718265 2011 8 21978 3.712985712985713 2011 9 19021 3.683507702013564 2011 10 18351 3.679363522423846 2011 11 19119 3.679951880328469 2011 12 18745 3.6682848759669247 2012 1 24760 3.714983844911147 2012 2 22946 3.691405909526715 2012 3 24115 3.6799502384408043 2012 4 22739 3.688640661418708 2012 5 23057 3.662488615171098 2012 6 24039 3.689171762552519 2012 7 26276 3.6703075049474805 2012 8 24990 3.6781512605042015 2012 9 23147 3.6746014602324277 2012 10 23870 3.661164641809803 2012 11 23184 3.6808143547273984 2012 12 23447 3.6537723376124878 2013 1 30683 3.7059609555780075 2013 2 26903 3.672861762628703 2013 3 31257 3.6810954346226445 2013 4 29867 3.6755616566779388 2013 5 30846 3.654282565000324 2013 6 31067 3.6693597708179095 2013 7 33650 3.6796136701337296 2013 8 36543 3.69236242235175 2013 9 33794 3.6862164881339883 2013 10 32929 3.6864162288560234 2013 11 33303 3.702128937332973 2013 12 33108 3.6926724658692764 2014 1 39359 3.741990396097462 2014 2 35093 3.715812270253327 2014 3 43159 3.73518848907528 2014 4 40633 3.7264046464696183 2014 5 43917 3.7156226518204796 2014 6 43973 3.720669501739704 2014 7 50066 3.7178724084208845 2014 8 50220 3.721883711668658 2014 9 43419 3.7221262580897765 2014 10 44580 3.7397039030955583 2014 11 43462 3.7304771984722285 2014 12 44394 3.6898680001802044 2015 1 53951 3.7497544067765194 2015 2 49653 3.7175195859263286 2015 3 56777 3.717262271694524 2015 4 54848 3.7528077596266045 2015 5 58458 3.7233740463238565 2015 6 59144 3.7401596104423103 2015 7 64940 3.7597474591931013 2015 8 65805 3.747420408783527 2015 9 57164 3.7495801553425

#Writing transformed data back to AWS S3 storage in the transformed-data folder

In [0]:
output_path = "dbfs:/mnt/de-yelpdataset-raw/yelpdataset/transformed-data/"

business_insights.write.mode("overwrite").parquet(output_path + "business_insights")
user_insights.write.mode("overwrite").parquet(output_path + "user_insights")
time_aggregates.write.mode("overwrite").parquet(output_path + "time_aggregates")

# Now to Verify Transformed Data

print("\nSample Data from Business Insights:")
spark.read.parquet(output_path + "business_insights").show(5)

print("\nSample Data from User Insights:")
spark.read.parquet(output_path + "user_insights").show(5)

print("\nSample Data from Time-Based Aggregates:")
spark.read.parquet(output_path + "time_aggregates").show(5)


Sample Data from Business Insights:
+--------------------+--------------------+--------------------+-------------+-----+-------------+--------------+
|         business_id|                name|          categories|         city|state|total_reviews|average_rating|
+--------------------+--------------------+--------------------+-------------+-----+-------------+--------------+
|1RqfozJoosHAsKZhc...|Walls Jewelry Rep...|Watch Repair, Loc...|    Nashville|   TN|          114|           5.0|
|-siOxQQcGKtb-04dX...|ella & louie flowers|Flowers & Gifts, ...|Santa Barbara|   CA|          104|           5.0|
|4-P4Bzqd01YvKX9tp...|       Drink & Learn|Beer, Wine & Spir...|  New Orleans|   LA|           90|           5.0|
|dhLARBhUnJloLa8xZ...|Steves iPhone Repair|Professional Serv...|  Cherry Hill|   NJ|           78|           5.0|
|LTqm4uY4GIYHfzuh5...|Jeramie Lu Photog...|Event Photography...|         Reno|   NV|           77|           5.0|
+--------------------+--------------------+--------